In [119]:
import math
import time
import os
import sys
from queue import LifoQueue
import numpy as np
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

In [120]:
class Puzzle: # A class to represent the properties of the puzzle
    def __init__(self,tiles):
        self.size = int(math.sqrt(len(tiles))) # defining length/width of the Puzzle
        self.tiles = tiles

    # Function to get list of possible scenarios of the puzzle for each possible action
    def get_result_of_action(self,action):
        result_tiles = self.tiles[:]
        empty_index = result_tiles.index('0')
        if action=='L':
            if empty_index%self.size>0:
                result_tiles[empty_index-1],result_tiles[empty_index] = result_tiles[empty_index],result_tiles[empty_index-1]
        if action=='R':
            if empty_index%self.size<(self.size-1): 
                result_tiles[empty_index+1],result_tiles[empty_index] = result_tiles[empty_index],result_tiles[empty_index+1]
        if action=='U':
            if empty_index-self.size>=0:
                result_tiles[empty_index-self.size],result_tiles[empty_index] = result_tiles[empty_index],result_tiles[empty_index-self.size]
        if action=='D':
            if empty_index+self.size < self.size*self.size:
                result_tiles[empty_index+self.size],result_tiles[empty_index] = result_tiles[empty_index],result_tiles[empty_index+self.size]
        return Puzzle(result_tiles)


In [121]:
class Node: # A class to represent a node in the graph
    def __init__(self,state,parent,action):
        self.state = state
        self.parent = parent
        self.action = action

    # __repr__ helps represent objects as a string
    def __repr__(self):
        return str(self.state.tiles)

    # Defining the rules to compare two nodes of class type "Node"
    def __eq__(self,other):
        return self.state.tiles == other.state.tiles


In [122]:
class PriorityQueue(object):
    
    def __init__(self):
        self.queue = []
        
    # for checking if the queue is empty
    def isEmpty(self):
        return len(self.queue) == 0
    
    # for inserting an element in the queue
    def append(self, element):
        self.queue.append(element)
  
    # for popping an element based on Priority i.e. low value of evaluation function in this case
    def pop(self, heuristic_type, goal):
            min = 0
            for i in range(len(self.queue)):
                if eval_function(self.queue[i], heuristic_type, goal) < eval_function(self.queue[min], heuristic_type, goal):
                    min = i
            p = self.queue[min]
            del self.queue[min]
            return p


In [123]:
def get_children(parent_node): # Expands the given node to get its children nodes
    children = []
    actions = ['L','R','U','D']
    for action in actions:
        child_state = parent_node.state.get_result_of_action(action)
        child_node = Node(child_state,parent_node,action)
        children.append(child_node)
    return children

In [124]:
def find_path(node): # Function to calculate the path traveled (or) the order of actions performed from initial state to reach the given state
    path = []
    while(node.parent is not None):
        path.append(node.action)
        node = node.parent
    path.reverse()
    return path

In [125]:
def depth_of_node(node): # Calculates the depth of a given node. This can be used as the cost [g(n)] of the node when calculating the node's evaluation function [f(n)]
    depth = 0
    while(node.parent is not None):
        depth = depth + 1
        node = node.parent
    return depth

In [126]:
# Calculates manhattan distance for a given node/state from the goal state. 'g' represents goal state
def manhattan_distance(node, g):
    s = node.state.size
    G = np.array(g)
    G = np.reshape(G, (s,s))
    T = np.array(node.state.tiles)
    T = np.reshape(T, (s,s))
    md = 0
    for j in node.state.tiles:
        x_val,y_val = np.where(T == j)
        x_goal,y_goal = np.where(G == j)
        md = abs(x_val - x_goal) + abs(y_val - y_goal) + md
    return md

In [127]:
# Function to return number of misplaced tiles in the given node/state. 'g' represents goal state
def num_of_misplaced_tiles(node, g):
    n = node.state.tiles
    nmt = 0                     # number of misplaced tiles
    for i in range(len(g)):
        if not n[i] == g[i]:
            nmt = nmt + 1
    return nmt

In [128]:
# Calculates the value of evaluation function f(n) where f(n) = g(n) {or} f(n) = h(n).
# g(n) : depth or cost of the node
# h(n) : manhattan distance or number of misplaced tiles
def eval_function(node, heuristic, goal):
    if(heuristic == "Manhattan distance"):
        f = depth_of_node(node) + manhattan_distance(node, goal)
    elif (heuristic == "Number of misplaced tiles"):
        f = depth_of_node(node) + num_of_misplaced_tiles(node, goal)
    return f

In [129]:
def IDA_star(root, h_type, goal):
    path = []
    bound = eval_function(root, h_type, goal)
    path.append(root)
    while True:
        t, p = a_star(path, goal, bound, h_type)
        if t == "FOUND" : 
            return bound, p, t
        if t == float("inf"): return "NOT FOUND", None, None
        bound = t

In [130]:
def a_star(path, goal_state, limit, heuristic_type):
    
    node = path[-1]
    f = eval_function(node, heuristic_type, goal_state)
    if f > limit: return f, None
    if node.state.tiles == goal_state : 
        return "FOUND", find_path(node)
    min = float("inf")
    
    children_nodes = get_children(node)
#    NodesExpanded.append(node)
    
    # Sorting children nodes in ascending order of their evaluation function
    for i in range(0,len(children_nodes)):
        for j in range(i+1,len(children_nodes)):
            if eval_function(children_nodes[i],heuristic_type, goal_state) > eval_function(children_nodes[j], heuristic_type, goal_state):
                temp = children_nodes[i]
                children_nodes[i] = children_nodes[j]
                children_nodes[j] = temp
                
    for child in children_nodes :
        if child not in path:
            path.append(child)
            t, nd = a_star(path, goal_state, limit, heuristic_type)
            if t == "FOUND": return "FOUND", nd
            if t < min: min = t
            path.pop()
    
    return min, None

In [131]:
# # ------------------------- ITERATIVE DEEPENING A-STAR Search -------------------------------- #
# def IDA_star(root, goal, h_type):
#     limit = eval_function(root, h_type, goal)
#     goal_reached = False
#     nIterations = 0
#     while (goal_reached == False):
#         ExpandedNodes = []
#         path, nExpandedNodes, goal_reached, mem, f = a_star(root, goal, limit, h_type, ExpandedNodes)
#         limit = f
#         nIterations = nIterations + 1
#         print(f)
#     return path, nExpandedNodes, mem, nIterations
# # ---------------------------------------------------------------------------------------------

In [132]:
# def a_star(node, goal_state, limit, heuristic_type, NodesExpanded):
    
#     print("Visiting node : " + str(node.state.tiles))
#     print(str(eval_function(node, heuristic_type, goal_state)))
#     if(goal_state == node.state.tiles):
#             p = find_path(node)
#             return p,len(NodesExpanded), True, max(0, sys.getsizeof(NodesExpanded)), None
    
#     f = eval_function(node, heuristic_type, goal_state)
    
#     if (f > limit):
#         print("Breached threshold with value : " + str(f))
#         return None,None, False, None, f
    
#     children_nodes = get_children(node)
#     NodesExpanded.append(node)
    
#     min = float("inf")
    
#     # Sorting children nodes in ascending order of their evaluation function
#     for i in range(0,len(children_nodes)):
#         for j in range(i+1,len(children_nodes)):
#             if eval_function(children_nodes[i],heuristic_type, goal_state) > eval_function(children_nodes[j], heuristic_type, goal_state):
#                 temp = children_nodes[i]
#                 children_nodes[i] = children_nodes[j]
#                 children_nodes[j] = temp
        
#     for child in children_nodes :
# #   for chosen_node in list(sorted_dict.keys()):
#         if (child not in NodesExpanded):
#             p, nNodesExpanded, goal_reached, mem, evalFunc = a_star(child, goal_state, limit, heuristic_type, NodesExpanded)
#             if ( evalFunc == None ):
#                 return p, nNodesExpanded, goal_reached, mem, evalFunc
#             elif (evalFunc < min):
#                 min = evalFunc
    
#     return None, len(NodesExpanded), False, None, min

In [ ]:
#initial = ['1','0','2','4','5','7','3','8','9','6','11','12','13','10','14','15']
#initial = ['5', '2', '4', '8', '10', '3', '11', '14', '6', '0', '9', '12', '13', '1', '15', '7']
#initial = ['1','3','4','8','5','0','2','6','9','10','7','11','13','14','15','12']
initial = ['5', '2', '4', '8', '10', '0', '3', '14', '13', '6', '11', '12', '1', '15', '9', '7']

#initial = str(input("initial configuration: "))
initial_list = initial
root = Node(Puzzle(initial_list),None,None)
#heuristics = ["Number of misplaced tiles","Manhattan distance"]
heuristics = ["Manhattan distance"]
goal_state = ['1','2','3','4','5','6','7','8','9','10','11','12','13','14','15','0']

for heuristic in heuristics:
    #heuristic = i
    print("--------------Heuristic : "+ heuristic +" -------------------")
    start_time = time.time()
    r, pth, st = IDA_star(root, heuristic, goal_state)
    end_time = time.time()
    print(st)
    print(r)
    print(pth)
    print(str(end_time - start_time))

--------------Heuristic : Manhattan distance -------------------


In [152]:
# #initial = ['1','0','2','4','5','7','3','8','9','6','11','12','13','10','14','15']
# initial = ['5', '2', '4', '8', '10', '3', '11', '14', '6', '0', '9', '12', '13', '1', '15', '7']
# #initial = ['1','3','4','8','5','0','2','6','9','10','7','11','13','14','15','12']

# #initial = str(input("initial configuration: "))
# initial_list = initial
# root = Node(Puzzle(initial_list),None,None)
# #heuristics = ["Number of misplaced tiles","Manhattan distance"]
# heuristics = ["Manhattan distance"]
# goal_state = ['1','2','3','4','5','6','7','8','9','10','11','12','13','14','15','0']

# for heuristic in heuristics:
#     #heuristic = i
#     print("--------------Heuristic : "+ heuristic +" -------------------")
#     start_time = time.time()
#     path, expanded_nodes, memory_used, iterations = IDA_star(root, goal_state, heuristic)
#     end_time = time.time()
#     print("Moves: " , path)
#     print("Number of expanded Nodes: "+ str(expanded_nodes))
#     print("Time Taken: " + str(end_time - start_time))
#     print("Max Memory (Bytes): " +  str(memory_used))
#     print("Num of iterations: " +  str(iterations))
#     print("\n")

--------------Heuristic : Manhattan distance -------------------
Visiting node : ['5', '2', '4', '8', '10', '3', '11', '14', '6', '0', '9', '12', '13', '1', '15', '7']
[26]
Visiting node : ['5', '2', '4', '8', '10', '3', '11', '14', '6', '9', '0', '12', '13', '1', '15', '7']
[25]
Visiting node : ['5', '2', '4', '8', '10', '3', '11', '14', '6', '9', '12', '0', '13', '1', '15', '7']
[26]
Visiting node : ['5', '2', '4', '8', '10', '3', '11', '14', '6', '9', '12', '7', '13', '1', '15', '0']
[25]
Visiting node : ['5', '2', '4', '8', '10', '3', '11', '14', '6', '9', '12', '7', '13', '1', '0', '15']
[28]
Breached threshold with value : [28]
Visiting node : ['5', '2', '4', '8', '10', '3', '11', '0', '6', '9', '12', '14', '13', '1', '15', '7']
[27]
Breached threshold with value : [27]
Visiting node : ['5', '2', '4', '8', '10', '3', '0', '14', '6', '9', '11', '12', '13', '1', '15', '7']
[26]
Visiting node : ['5', '2', '4', '8', '10', '3', '14', '0', '6', '9', '11', '12', '13', '1', '15', '7']
[2

Visiting node : ['5', '2', '4', '8', '6', '10', '3', '14', '0', '9', '11', '12', '13', '1', '15', '7']
[27]
Visiting node : ['5', '2', '4', '8', '6', '10', '3', '14', '9', '0', '11', '12', '13', '1', '15', '7']
[26]
Visiting node : ['5', '2', '4', '8', '6', '10', '3', '14', '9', '1', '11', '12', '13', '0', '15', '7']
[25]
Visiting node : ['5', '2', '4', '8', '6', '10', '3', '14', '9', '1', '11', '12', '13', '15', '0', '7']
[26]
Visiting node : ['5', '2', '4', '8', '6', '10', '3', '14', '9', '1', '11', '12', '13', '15', '7', '0']
[25]
Visiting node : ['5', '2', '4', '8', '6', '10', '3', '14', '9', '1', '11', '0', '13', '15', '7', '12']
[28]
Visiting node : ['5', '2', '4', '8', '6', '10', '3', '0', '9', '1', '11', '14', '13', '15', '7', '12']
[29]
Visiting node : ['5', '2', '4', '0', '6', '10', '3', '8', '9', '1', '11', '14', '13', '15', '7', '12']
[30]
Breached threshold with value : [30]
Visiting node : ['5', '2', '4', '8', '6', '10', '0', '3', '9', '1', '11', '14', '13', '15', '7', '1

Breached threshold with value : [31]
Visiting node : ['5', '2', '14', '4', '6', '10', '3', '8', '9', '1', '11', '12', '0', '13', '15', '7']
[30]
Visiting node : ['5', '2', '14', '4', '6', '10', '3', '8', '0', '1', '11', '12', '9', '13', '15', '7']
[33]
Breached threshold with value : [33]
Visiting node : ['5', '2', '14', '4', '6', '0', '3', '8', '9', '10', '11', '12', '13', '1', '15', '7']
[29]
Visiting node : ['5', '2', '14', '4', '0', '6', '3', '8', '9', '10', '11', '12', '13', '1', '15', '7']
[30]
Visiting node : ['0', '2', '14', '4', '5', '6', '3', '8', '9', '10', '11', '12', '13', '1', '15', '7']
[31]
Breached threshold with value : [31]
Visiting node : ['5', '2', '14', '4', '9', '6', '3', '8', '0', '10', '11', '12', '13', '1', '15', '7']
[31]
Breached threshold with value : [31]
Visiting node : ['5', '2', '14', '4', '6', '3', '0', '8', '9', '10', '11', '12', '13', '1', '15', '7']
[30]
Visiting node : ['5', '2', '14', '4', '6', '3', '8', '0', '9', '10', '11', '12', '13', '1', '15'

[32]
Breached threshold with value : [32]
Visiting node : ['5', '2', '4', '8', '6', '3', '0', '14', '9', '10', '11', '12', '13', '1', '15', '7']
[28]
Visiting node : ['5', '2', '4', '8', '6', '3', '14', '0', '9', '10', '11', '12', '13', '1', '15', '7']
[27]
Visiting node : ['5', '2', '4', '0', '6', '3', '14', '8', '9', '10', '11', '12', '13', '1', '15', '7']
[28]
Visiting node : ['5', '2', '0', '4', '6', '3', '14', '8', '9', '10', '11', '12', '13', '1', '15', '7']
[29]
Visiting node : ['5', '0', '2', '4', '6', '3', '14', '8', '9', '10', '11', '12', '13', '1', '15', '7']
[32]
Breached threshold with value : [32]
Visiting node : ['5', '2', '4', '8', '6', '3', '14', '12', '9', '10', '11', '0', '13', '1', '15', '7']
[28]
Visiting node : ['5', '2', '4', '8', '6', '3', '14', '12', '9', '10', '11', '7', '13', '1', '15', '0']
[27]
Visiting node : ['5', '2', '4', '8', '6', '3', '14', '12', '9', '10', '11', '7', '13', '1', '0', '15']
[30]
Visiting node : ['5', '2', '4', '8', '6', '3', '14', '12'

Visiting node : ['5', '2', '4', '8', '3', '6', '14', '12', '10', '9', '0', '7', '13', '1', '11', '15']
[33]
Breached threshold with value : [33]
Visiting node : ['5', '2', '4', '8', '3', '6', '14', '12', '10', '9', '11', '7', '13', '0', '1', '15']
[33]
Breached threshold with value : [33]
Visiting node : ['5', '2', '4', '8', '3', '6', '14', '12', '10', '9', '0', '11', '13', '1', '15', '7']
[31]
Breached threshold with value : [31]
Visiting node : ['5', '2', '0', '8', '3', '6', '4', '14', '10', '9', '11', '12', '13', '1', '15', '7']
[31]
Breached threshold with value : [31]
Visiting node : ['5', '2', '4', '8', '3', '0', '6', '14', '10', '9', '11', '12', '13', '1', '15', '7']
[31]
Breached threshold with value : [31]
Visiting node : ['5', '2', '4', '8', '3', '6', '11', '14', '10', '9', '15', '12', '13', '1', '0', '7']
[28]
Visiting node : ['5', '2', '4', '8', '3', '6', '11', '14', '10', '9', '15', '12', '13', '1', '7', '0']
[27]
Visiting node : ['5', '2', '4', '8', '3', '6', '11', '14', 

...

Visiting node : ['5', '2', '3', '4', '10', '1', '0', '8', '6', '9', '14', '12', '13', '15', '11', '7']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '10', '1', '14', '8', '6', '9', '12', '0', '13', '15', '11', '7']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '10', '1', '14', '8', '6', '0', '9', '12', '13', '15', '11', '7']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '2', '3', '4', '10', '1', '14', '0', '6', '9', '11', '8', '13', '15', '7', '12']
[35]
Visiting node : ['5', '2', '3', '0', '10', '1', '14', '4', '6', '9', '11', '8', '13', '15', '7', '12']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '10', '1', '0', '14', '6', '9', '11', '8', '13', '15', '7', '12']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '10', '1', '14', '8', '6', '9', '7', '11', '13', '15', '0', '12']
[32]
Visiting node : ['5', '2', '3', '4', '10', '1', '14', '8', 

Visiting node : ['5', '2', '3', '4', '6', '10', '1', '0', '9', '7', '11', '8', '13', '14', '15', '12']
[37]
Visiting node : ['5', '2', '3', '0', '6', '10', '1', '4', '9', '7', '11', '8', '13', '14', '15', '12']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '2', '3', '4', '6', '10', '0', '1', '9', '7', '11', '8', '13', '14', '15', '12']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '2', '3', '4', '6', '10', '1', '8', '9', '7', '15', '11', '13', '14', '0', '12']
[36]
Visiting node : ['5', '2', '3', '4', '6', '10', '1', '8', '9', '7', '15', '11', '13', '14', '12', '0']
[37]
Visiting node : ['5', '2', '3', '4', '6', '10', '1', '8', '9', '7', '15', '0', '13', '14', '12', '11']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '2', '3', '4', '6', '10', '1', '8', '9', '7', '15', '11', '13', '0', '14', '12']
[39]
Breached threshold with value : [39]
Visiting node : ['5', '2', '3', '4', '6', '10', '0', '8', '9', '7', '1', '11', '13', '14', '15',

Visiting node : ['5', '2', '3', '4', '6', '1', '8', '11', '9', '10', '14', '12', '13', '15', '0', '7']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '6', '1', '8', '11', '9', '10', '0', '14', '13', '15', '7', '12']
[39]
Breached threshold with value : [39]
Visiting node : ['5', '2', '3', '0', '6', '1', '8', '4', '9', '10', '14', '11', '13', '15', '7', '12']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '6', '1', '14', '8', '9', '10', '0', '11', '13', '15', '7', '12']
[35]
Visiting node : ['5', '2', '3', '4', '6', '1', '14', '8', '9', '10', '11', '0', '13', '15', '7', '12']
[34]
Visiting node : ['5', '2', '3', '4', '6', '1', '14', '8', '9', '10', '11', '12', '13', '15', '7', '0']
[33]
Visiting node : ['5', '2', '3', '4', '6', '1', '14', '8', '9', '10', '11', '12', '13', '15', '0', '7']
[36]
Visiting node : ['5', '2', '3', '4', '6', '1', '14', '8', '9', '10', '11', '12', '13', '0', '15', '7']
[37]
Visiting node : ['5', '2'

Visiting node : ['5', '2', '3', '4', '10', '9', '1', '8', '6', '7', '11', '12', '13', '14', '0', '15']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '10', '9', '1', '0', '6', '7', '11', '8', '13', '14', '15', '12']
[39]
Breached threshold with value : [39]
Visiting node : ['5', '2', '3', '4', '10', '9', '1', '8', '6', '7', '15', '11', '13', '14', '0', '12']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '2', '3', '4', '10', '9', '0', '8', '6', '7', '1', '11', '13', '14', '15', '12']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '2', '3', '4', '10', '0', '1', '8', '6', '9', '7', '11', '13', '14', '15', '12']
[37]
Visiting node : ['5', '2', '3', '4', '10', '1', '0', '8', '6', '9', '7', '11', '13', '14', '15', '12']
[36]
Visiting node : ['5', '2', '3', '4', '10', '1', '7', '8', '6', '9', '0', '11', '13', '14', '15', '12']
[35]
Visiting node : ['5', '2', '3', '4', '10', '1', '7', '8', '6', '9', '11', '0', '13', '14', '15',

Visiting node : ['5', '1', '2', '0', '6', '10', '3', '4', '9', '7', '11', '8', '13', '14', '15', '12']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '1', '2', '4', '6', '10', '0', '3', '9', '7', '11', '8', '13', '14', '15', '12']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '1', '2', '4', '6', '10', '3', '8', '9', '7', '15', '11', '13', '14', '0', '12']
[36]
Visiting node : ['5', '1', '2', '4', '6', '10', '3', '8', '9', '7', '15', '11', '13', '14', '12', '0']
[37]
Visiting node : ['5', '1', '2', '4', '6', '10', '3', '8', '9', '7', '15', '0', '13', '14', '12', '11']
[40]
Breached threshold with value : [40]
Visiting node : ['5', '1', '2', '4', '6', '10', '3', '8', '9', '7', '15', '11', '13', '0', '14', '12']
[39]
Breached threshold with value : [39]
Visiting node : ['5', '1', '2', '4', '6', '10', '0', '8', '9', '7', '3', '11', '13', '14', '15', '12']
[38]
Breached threshold with value : [38]
Visiting node : ['5', '1', '2', '4', '6', '0', '3', '8', '9